# INVENTA - Prioritization of natural extracts for chemical originality discovery


In [2]:
from __future__ import print_function
from IPython.core.display import HTML
HTML("<script>Jupyter.notebook.kernel.restart()</script>")
import numpy as np
import pandas as pd
import sys 
import lineup_widget
import ipywidgets as widgets
from ipywidgets import *
!jupyter nbextension enable --py --sys-prefix lineup_widget


sys.path.append('../src')
sys.path.append('../gnps_postprocessing/src') 

from import_data import*
from process_data import *
from FC import *
from LC import *
from SC import *
from CC import *
from plot import *

from gnps_download_results import *
from consolidates_structures import *
from gnps_results_postprocess import *

Enabling notebook extension lineup_widget/extension...
      - Validating: OK


# Paths and parameters to define

In [3]:
#paths:

metadata_filename = '../data/Celastraceae_Set_metadata_pos.tsv'                      # The path were you want your folder to be placed
quantitative_data_filename = '../data/Celastraceae_pos_quant.csv'                    # The path were you want your GNPS job folder to be placed
tima_results_filename = '../data/Celastraceae_pos_spectral_match_results_repond.tsv' # ISDB_annot_LP_plantfungi_set # The name you want to give to your project, output resulst in data_out/project_name
vectorized_data_filename = '../data/Celastraceae_memomatrix.csv'                     # the path for your output to be stored in
canopus_npc_summary_filename = '../data/canopus_npc_summary.tsv'                     # Path to your spectral library file
sirius_annotations_filename = '../data/compound_identifications.tsv'                 # Path to the metadata of the spectral file

job_id=  '4c919fcbc83d487493a487012afb920a'  #"yourjobidgoeshere"  

# metadata headers

species_column = 'ATTRIBUTE_Species'
genus_column = 'ATTRIBUTE_Genus'
family_column = 'ATTRIBUTE_Family'
organe_column = 'ATTRIBUTE_Organe'
filename_header = 'filename'

# parameters for cleaning-up annotations from GNPS 

max_ppm_error = 5                 # min error in ppm to consider an annotation valable
shared_peaks = 4                 # min number of shared peaks between the MS2 experimental and MS2 from the database, to consider an annotation valable
min_cosine = 0.6                  # min cosine score to consider an annotation valable
ionisation_mode = 'pos'           # ionisation mode according to experimental conditions 'pos' or 'neg'
max_spec_charge = 2

#Feature_component

min_specificity = 0.90            # minimun feature specificity to consider

## inputs to use: 
isdb_annotations = True          # True: the tima_results_filename will be considered in the calculations
sirius_annotations = True        #True: the sirius_annotations_filename will be considered in the calculations

## cut-offs: 
min_score_final = 0.3             #cut-off filter for considering an isdb annotation valable. You must be extremenly carefull with this parameter, '0.0' as default.
min_ZodiacScore = 0.9             #cut-off filter for considering a sirius annotation valable. It is used in combination with min_ConfidenceScore.
min_ConfidenceScore= 0.25         #cut-off filter for considering a sirius annotation valable. '0.0' as default.

annotation_preference = 0          # Only Annotated features: '1' or  Only Not annotated features: '0'

#Literature_component

LC_component = True               # LC will be calculated

max_comp_reported_sp = 20          # max number of compounds reported at species level, more than this value, the plant is considered less interesting
max_comp_reported_g = 50         # max number of compounds reported at genus level,more than this value, the plant is considered less interesting
max_comp_reported_f = 500           # max number of compounds reported at genus level,more than this value, the plant is considered less interesting

#weight for each taxonomic level 
ws = 1
wg = 1
wf = 1 

#Similarity_component

SC_component = True                # SC will be calculated

#Class_component

CC_component = True               # CC will be calculated
min_class_confidence = 0.8       #cut-off filter for considering a sirius class valable. It is used in combination with min_recurrence.
min_recurrence = 5               # minimum recurrence of a chemical class to consider it acceptable

#specify the weight to modulate each component 
w1 = 1           # 1 means the value itself is taken into account. A 0.5 means onle half of the calculated value is taken into account
w2 = 1
w3 = 1
w4 = 1


# Prepare input files

### Download and clean the GNPS results

In [4]:
df_annotations = gnps_download_results(job_id, output_folder ='../data/all_annotations', return_annotation_table=True)
#df_annotations.head()

# Consolidate structure identifiers
gnps_annotations_consolidated  = consolidate_and_convert_structures(df_annotations, prefix='', smiles='Smiles', inchi='INCHI')

# Filter GNPS annotations
gnps_annotations_filtered = gnps_filter_annotations(gnps_annotations_consolidated, 'Consol_InChI', ionisation_mode, max_ppm_error, min_cosine, shared_peaks, max_spec_charge)

# Generate annotation attributes
annot_gnps_df = get_gnps_annotations(get_molecular_formula_from_inchi(gnps_annotations_filtered, 'Consol_InChI'))
#annot_gnps_df.head(2)


This is the GNPS job link: https://gnps.ucsd.edu/ProteoSAFe/status.jsp?task=4c919fcbc83d487493a487012afb920a


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 38.9M    0 38.9M    0     0  1601k      0 --:--:--  0:00:24 --:--:-- 3588k


GNPS job results were succesfully downloaded as: ../data/all_annotations.zip
GNPS job results were succesfully extracted into the folder: ../data/all_annotations
   FEATURE-BASED MOLECULAR NETWORKING job detected - Version > 28
      1835 spectral library annotations in the job.
      14969 nodes in the network (including single nodes).
Both SMILES and InChI were inputted
Converting SMILES to mol object
Succesfully converted to mol object: 1399
Exception to the parsing: 0
Not available: 437
Converting INCHI to mol object


RDKit ERROR: [11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 
[11:44:14] ERROR: 

Succesfully converted to mol object: 1513
Exception to the parsing: 0
Not available: 323
Consolidating the lists
Total mol object from the list 1 = 1399
Mol object consolidated from list 2 = 174
Consolidated structures = 1573
Converting mol objects to SMILES iso
Converting mol objects to SMILES
Converting mol objects to InChI
Converting mol objects to InChIKey
End
Initial number of annotations: 1836
Remaining after ionisation mode filtering: 1787
Remaining after max_ppm_error filtering: 1419
Remaining after min_cosine filtering: 1419
Remaining after number of shared_peaks filtering: 1419
Remaining after number of spectrum charge filtering: 1419
Initial number of annotations filtering: 1419
After carbon containing adducts filtering: 1419
Valid molecular formula: 1215


### Metadata table

In [5]:
metadata_df = pd.read_csv(metadata_filename, sep='\t')
metadata_df.head(3)

filename ATTRIBUTE_Code ATTRIBUTE_Type ATTRIBUTE_Family  \
0  LQ-01-61-01_pos.mzXML        V107694         Sample     Celastraceae   
1  LQ-01-61-02_pos.mzXML        V107695         Sample     Celastraceae   
2  LQ-01-61-03_pos.mzXML        V107696         Sample     Celastraceae   

  ATTRIBUTE_Genus ATTRIBUTE_Species ATTRIBUTE_Organe ATTRIBUTE_Broad_organ  \
0           Catha      Catha edulis           Leaves        photosynthetic   
1           Catha      Catha edulis            Stems      woody vegetative   
2           Catha      Catha edulis            Roots                 roots   

  ATTRIBUTE_Tissue ATTRIBUTE_Subsystem  
0     green tissue         aboveground  
1     woody tissue         aboveground  
2      root tissue         belowground

In [6]:
#if you need to create an unique identifier column like Species|part, use as model the followin line. IF the colum is PRESENT, then don't run it.
metadata_df['ATTRIBUTE_Sppart'] = metadata_df[species_column]+ "|" + metadata_df[organe_column].map(str)

In [7]:
col_id_unique = filename_header #'ATTRIBUTE_Sppart'  # filename_header   #column containing an unique identifier for each sample, like Species_plantpart, Species_solvent. It could be the filename

### Quantification table

In [8]:
#Quantitative table
quant_df = quant_table(pd.read_csv(quantitative_data_filename, sep=',',  index_col='row ID'))
quant_df.head(3)

LQ-01-61-01_pos.mzXML  LQ-01-61-02_pos.mzXML  LQ-01-61-03_pos.mzXML  \
row ID                                                                        
1                    1.000000               0.050224               0.014338   
2                    0.340676               0.031479               0.001481   
3                    0.328540               0.041562               0.000000   

        LQ-01-61-04_pos.mzXML  LQ-01-61-05_pos.mzXML  LQ-01-61-06_pos.mzXML  \
row ID                                                                        
1                    0.031273                    0.0                    0.0   
2                    1.000000                    0.0                    0.0   
3                    0.208271                    0.0                    0.0   

        LQ-01-61-07_pos.mzXML  LQ-01-61-08_pos.mzXML  LQ-01-61-09_pos.mzXML  \
row ID                                                                        
1                         0.0                    0.0               0.008821   
2                         0.0                    0.0               0.004442   
3                         0.0                    0.0               0.000000   

        LQ-01-61-10_pos.mzXML  ...  LQ-01-61-69_pos.mzXML  \
row ID                         ...                          
1                         0.0  ...                    0.0   
2                         0.0  ...                    0.0   
3                         0.0  ...                    0.0   

        LQ-01-61-70_pos.mzXML  LQ-01-61-71_pos.mzXML  LQ-01-61-72_pos.mzXML  \
row ID                                                                        
1                         0.0                    0.0                    0.0   
2                         0.0                    0.0                    0.0   
3                         0.0                    0.0                    0.0   

        LQ-01-61-73_pos.mzXML  LQ-01-61-74_pos.mzXML  LQ-01-61-75_pos.mzXML  \
row ID                                                                        
1                         0.0                    0.0                    0.0   
2                         0.0                    0.0                    0.0   
3                         0.0                    0.0                    0.0   

        LQ-01-61-76_pos.mzXML  LQ-01-61-77_pos.mzXML  LQ-01-61-78_pos.mzXML  
row ID                                                                       
1                         0.0                    0.0                    0.0  
2                         0.0                    0.0                    0.0  
3                         0.0                    0.0                    0.0  

[3 rows x 78 columns]

#### Combined and remove experimental controls 


In [12]:
# merge tables
full_df = full_data(metadata_df, quant_df, filename_header)
#full_df.head(2)

#erase all the blanks and QC's - Change the string as needed
list_of_strings_for_QC_Blank_filter = ['Blank', 'QC']
column_to_use_for_filtering = 'ATTRIBUTE_Type' #this information should be included in the metadata table

filtered_full_df = drop_samples_based_on_string(full_df,'full_df',list_of_strings_for_QC_Blank_filter, column_to_use_for_filtering)
filtered_metadata_df = drop_samples_based_on_string(metadata_df, 'metadata_df', list_of_strings_for_QC_Blank_filter, column_to_use_for_filtering)

(78, 14981)
(76, 14981)
(77, 11)
(76, 11)


##### Make a minimal table for further processing & apply filter by intensity 

In [13]:
reduced_df = reduce_df(filtered_full_df, filtered_metadata_df, col_id_unique).transpose()

In [14]:
#you can choose between a quantile filter (only the features higher than the third quantile (75%) ares kept):
reduced_df = quantile_filter(reduced_df, quantile_threshold=0.75)

In [17]:
#or a simple intensity filter, it removes the features less than X % of relative area (by default 20%). If you want you can combine boht filters
reduced_df = features_filter(reduced_df, min_threshold=0.02)

In [15]:
drop_down = widgets.Dropdown(options=reduced_df.columns,description='Sample to plot', disabled=False)
def dropdown_handler(change):
    global sample
    print(change.new)
    sample = change.new  # This line isn't working
drop_down.observe(dropdown_handler, names='value')
display(drop_down)

Dropdown(description='Sample to plot', options=('LQ-01-61-01_pos.mzXML', 'LQ-01-61-02_pos.mzXML', 'LQ-01-61-03…

In [18]:
distribution_to_plot(sample, quant_df, reduced_df)

# Start calculation the diferent components

# Feature component (FC)

#### FC.1. Annotation Rate

In [11]:
#load annotations files
annot_is_df       = get_isdb_annotations(tima_results_filename, isdb_annotations)
annot_sirius_df   = get_sirius_annotations(sirius_annotations_filename, sirius_annotations) 

annotation_df = annotations(annot_is_df, annot_sirius_df, sirius_annotations, isdb_annotations, min_score_final, min_ConfidenceScore, min_ZodiacScore)
annotation_df.head(2)


cluster index  componentindex Annotated_GNPS  Annotated_ISDB  \
0              1             113              0               1   
1              2             136              0               1   

   Annotated_Sirius  annotation  
0                 0           0  
1                 0           0

#### FC.2. FC computation

In [14]:
FC = feature_component(quant_df, reduced_df, annotation_df, metadata_df, family_column, genus_column, species_column, col_id_unique, min_specificity, annotation_preference, filename_header, annot_sirius_df, sirius_annotations, annot_gnps_df, min_ZodiacScore)
FC.head()

filename ATTRIBUTE_Family ATTRIBUTE_Genus  \
71  LQ-01-61-72_pos.mzXML     Celastraceae         Salacia   
76  LQ-01-61-78_pos.mzXML     Celastraceae      Pristimera   
36  LQ-01-61-37_pos.mzXML     Celastraceae        Euonymus   
6   LQ-01-61-07_pos.mzXML     Celastraceae       Celastrus   
55  LQ-01-61-56_pos.mzXML     Celastraceae        Maytenus   

        ATTRIBUTE_Species  initial_F  filtered_F  Total_SF  Total_SNAF  \
71     Salacia letestuana      478.0       254.0     187.0       178.0   
76      Pristimera indica      680.0        88.0      53.0        51.0   
36    Euonymus sanguineus      876.0        41.0      27.0        23.0   
6   Celastrus paniculatus      827.0       244.0     136.0       131.0   
55        Maytenus undata      709.0       132.0      79.0        69.0   

    Total_SNA_GQMFF  MF_prediction_ratio    FS    FC  
71              155                 0.61  0.74  0.70  
76               22                 0.25  0.60  0.58  
36               21                 0.51  0.66  0.56  
6               109                 0.45  0.56  0.54  
55               55                 0.42  0.60  0.52

In [13]:
#Show the results in an interactive way
interact(selection_changed_FC, selection=lineup_widget.LineUpWidget(FC));

/home/quirosgu/anaconda3/envs/inventa/lib/python3.7/site-packages/jupyter_client/session.py:718: UserWarning: Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant
  content = self.pack(content)


interactive(children=(LineUpWidget(value=[], description='selection', layout=Layout(align_self='stretch', heig…

#### Select the sample you wan to plot 

In [14]:
drop_down = widgets.Dropdown(options=quant_df.columns,description='Sample to plot', disabled=False)
def dropdown_handler(change):
    global sample
    print(change.new)
    sample = change.new  # This line isn't working
drop_down.observe(dropdown_handler, names='value')
display(drop_down)

Dropdown(description='Sample to plot', options=('LQ-01-61-01_pos.mzXML', 'LQ-01-61-02_pos.mzXML', 'LQ-01-61-03…

#### Plot the selected sample

In [18]:
hist_to_plot(sample, quantitative_data_filename, annotation_df, reduced_df, min_specificity, annotation_preference)

In [ ]:
#save the results for that particular sample 


# Literature component (LC)


#### LC.1. LC computation

In [ ]:
LC = literature_component(LC_component, metadata_df, filename_header, species_column, genus_column, family_column, max_comp_reported_sp, max_comp_reported_g, max_comp_reported_f, ws, wg, wf)
LC

filename ATTRIBUTE_Family ATTRIBUTE_Genus  \
0   LQ-01-61-01_pos.mzXML     Celastraceae           Catha   
1   LQ-01-61-02_pos.mzXML     Celastraceae           Catha   
2   LQ-01-61-03_pos.mzXML     Celastraceae           Catha   
3   LQ-01-61-04_pos.mzXML     Celastraceae           Catha   
4   LQ-01-61-05_pos.mzXML     Celastraceae       Celastrus   
..                    ...              ...             ...   
72  LQ-01-61-73_pos.mzXML     Celastraceae    Tripterygium   
73  LQ-01-61-74_pos.mzXML     Celastraceae    Tripterygium   
74  LQ-01-61-75_pos.mzXML     Celastraceae    Tripterygium   
75  LQ-01-61-76_pos.mzXML                0               0   
76  LQ-01-61-78_pos.mzXML     Celastraceae      Pristimera   

           ATTRIBUTE_Species  Reported_comp_Species  Reported_comp_Genus  \
0               Catha edulis                  126.0                126.0   
1               Catha edulis                  126.0                126.0   
2               Catha edulis                  126.0                126.0   
3               Catha edulis                  126.0                126.0   
4      Celastrus orbiculatus                  212.0                732.0   
..                       ...                    ...                  ...   
72  Tripterygium hypoglaucum                  162.0               1353.0   
73    Tripterygium wilfordii                 1011.0               1353.0   
74    Tripterygium wilfordii                 1011.0               1353.0   
75                         0                    0.0                  0.0   
76         Pristimera indica                    2.0                  8.0   

    Reported_comp_Family       LC  
0                 6064.0  0.79052  
1                 6064.0  0.79052  
2                 6064.0  0.79052  
3                 6064.0  0.79052  
4                 6064.0  0.62632  
..                   ...      ...  
72                6064.0  0.52712  
73                6064.0  0.10262  
74                6064.0  0.10262  
75                   0.0  1.00000  
76                6064.0  0.87612  

[77 rows x 8 columns]

# Similarity component (SC)

#### SC.1. SC computation

In [ ]:
metric_df = pd.read_csv(vectorized_data_filename, sep=',', encoding= 'unicode_escape')
SC = similarity_component(metric_df, SC_component)
SC

filename  anomaly_IF  anomaly_LOF  anomaly_OCSVM  SC
0   LQ-01-61-01_pos.mzXML           1            1              1   0
1   LQ-01-61-02_pos.mzXML           1            1              1   0
2   LQ-01-61-03_pos.mzXML          -1            1              1   1
3   LQ-01-61-04_pos.mzXML          -1            1              1   1
4   LQ-01-61-05_pos.mzXML           1            1              1   0
..                    ...         ...          ...            ...  ..
71  LQ-01-61-72_pos.mzXML           1           -1              1   1
72  LQ-01-61-73_pos.mzXML           1            1              1   0
73  LQ-01-61-74_pos.mzXML           1            1              1   0
74  LQ-01-61-75_pos.mzXML           1            1              1   0
75  LQ-01-61-78_pos.mzXML           1           -1             -1   1

[76 rows x 5 columns]

#### SC.2. Visualizing the outliers

NOTE: depending on the size of the data set, projections could take a while... 

#### SC.2.1 PCoA + UMAP combined visualization

In [ ]:
pcoa_umap_2d(
    matrix= metric_df,
    data = SC,
    metric= 'braycurtis', 
    filename_header=filename_header)

/home/quirosgu/anaconda3/envs/inventa/lib/python3.7/site-packages/skbio/stats/ordination/_principal_coordinate_analysis.py:152: RuntimeWarning:

The result contains negative eigenvalues. Please compare their magnitude with the magnitude of some of the largest positive eigenvalues. If the negative ones are smaller, it's probably safe to ignore them, but if they are large in magnitude, the results won't be useful. See the Notes section for more details. The smallest eigenvalue is -0.0016647020911528683 and the largest is 0.9032327317957183.



##### SC.2.2 optionally you can chosse to plot only UMAP, PCoA or PCoA 3d

In [ ]:
#umap_2d(matrix = metric_df,
#        data = SC, 
#        metadata=metadata_df, 
#        filename_header =filename_header)

In [ ]:
#pcoa_2d(
#    matrix= metric_df,
#    data = SC,
#    metric= 'braycurtis', 
#    filename_header=filename_header)

In [ ]:
#pcoa_3d(
#    matrix= metric_df,
 #   data = SC,
 #   metric= 'braycurtis',
 #   filename_header=filename_header)

# Class component (SC)

### CC.1. Retrive and clean the predicted chemical classes from Sirius

In [ ]:
canopus_npc_df = get_canopus_pred_classes(canopus_npc_summary_filename, CC_component)
CC = class_component(canopus_npc_df, filename_header, species_column, genus_column,family_column, metadata_df, reduced_df, col_id_unique, min_class_confidence, min_recurrence, CC_component)
CC

filename                                              class  \
0   LQ-01-61-02_pos.mzXML  {Oleanane triterpenoids, Lanostane, Tirucallan...   
1   LQ-01-61-06_pos.mzXML  {Agarofuran sesquiterpenoids, Tetracyclic dite...   
2   LQ-01-61-07_pos.mzXML  {Paraliane diterpenoids, Daucane sesquiterpeno...   
9   LQ-01-61-56_pos.mzXML                      {Agarofuran sesquiterpenoids}   
10  LQ-01-61-66_pos.mzXML  {Lanostane, Tirucallane and Euphane triterpeno...   
11  LQ-01-61-67_pos.mzXML  {Straight chain fatty acids, Ursane and Taraxa...   
14  LQ-01-61-73_pos.mzXML                               {Pyridine alkaloids}   
15  LQ-01-61-74_pos.mzXML  {Prenyl quinone meroterpenoids, Abietane diter...   
16  LQ-01-61-75_pos.mzXML             {Ursane and Taraxastane triterpenoids}   
17  LQ-01-61-78_pos.mzXML                      {Agarofuran sesquiterpenoids}   

           ATTRIBUTE_Species ATTRIBUTE_Genus ATTRIBUTE_Family  \
0               Catha edulis           Catha     Celastraceae   
1      Celastrus orbiculatus       Celastrus     Celastraceae   
2      Celastrus paniculatus       Celastrus     Celastraceae   
9            Maytenus undata        Maytenus     Celastraceae   
10         Salacia chinensis         Salacia     Celastraceae   
11         Salacia chinensis         Salacia     Celastraceae   
14  Tripterygium hypoglaucum    Tripterygium     Celastraceae   
15    Tripterygium wilfordii    Tripterygium     Celastraceae   
16    Tripterygium wilfordii    Tripterygium     Celastraceae   
17         Pristimera indica      Pristimera     Celastraceae   

                   Chemical_class_reported_in_species  \
0   {Flavonols, Monocyclic monoterpenoids, Pinane ...   
1   {Carotenoids (C40, β-ε), Labdane diterpenoids,...   
2   {Unsaturated fatty acids, Agarofuran sesquiter...   
9   {Lanostane, Tirucallane and Euphane triterpeno...   
10  {Megastigmanes, Furofuranoid lignans, Acyclic ...   
11  {Megastigmanes, Furofuranoid lignans, Acyclic ...   
14  {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
15  {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
16  {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
17                        {Cucurbitane triterpenoids}   

                     Chemical_class_reported_in_genus  \
0   {Flavonols, Monocyclic monoterpenoids, Pinane ...   
1   {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
2   {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
9   {Lanostane, Tirucallane and Euphane triterpeno...   
10  {Megastigmanes, Furofuranoid lignans, Acyclic ...   
11  {Megastigmanes, Furofuranoid lignans, Acyclic ...   
14  {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
15  {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
16  {Agarofuran sesquiterpenoids|Pyridine alkaloid...   
17                        {Cucurbitane triterpenoids}   

                                         New_CC_in_sp  \
0   {Lanostane, Tirucallane and Euphane triterpeno...   
1                          {Tetracyclic diterpenoids}   
2   {Paraliane diterpenoids, Daucane sesquiterpeno...   
9                       {Agarofuran sesquiterpenoids}   
10  {Lanostane, Tirucallane and Euphane triterpeno...   
11                       {Straight chain fatty acids}   
14                                                 {}   
15                    {Prenyl quinone meroterpenoids}   
16                                                 {}   
17                      {Agarofuran sesquiterpenoids}   

                                      New_CC_in_genus  CC  
0   {Oleanane triterpenoids, Lanostane, Tirucallan...   1  
1                          {Tetracyclic diterpenoids}   1  
2   {Paraliane diterpenoids, Daucane sesquiterpeno...   1  
9                       {Agarofuran sesquiterpenoids}   1  
10  {Lanostane, Tirucallane and Euphane triterpeno...   1  
11                       {Straight chain fatty acids}   1  
14                                                 {}   0  
15                    {Prenyl quinone meroterpenoids}   

# Priority rank Results

In [ ]:
PR = priority_rank(LC_component, SC_component, CC_component, w1, w2, w3, w4)
#PR.head()

In [ ]:
#Cyt_format_visualization = Cyt_format(col_id_unique)

### Display results

In [ ]:
#Show the results in an interactive way
#def selection_changed(selection):
#    return df.iloc[selection]
interact(selection_changed, selection=lineup_widget.LineUpWidget(PR));

/home/quirosgu/anaconda3/envs/inventa/lib/python3.7/site-packages/jupyter_client/session.py:718: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



interactive(children=(LineUpWidget(value=[], description='selection', layout=Layout(align_self='stretch', heig…

In [20]:
# implementation ION ID
quantitative_data_filename = '../data/Celastraceae_pos_quant_id.csv'
ID_df = pd.read_csv(quantitative_data_filename, sep=',',  index_col='row ID')
ID_df.head()


row m/z  row retention time  row ion mobility  \
row ID                                                     
1       127.013814            0.023983               NaN   
2       175.097948            0.029225               NaN   
3       159.066546            0.042933               NaN   
4       125.085131            0.050942               NaN   
5       200.093031            0.054469               NaN   

        row ion mobility unit  row CCS  correlation group ID  \
row ID                                                         
1                         NaN      NaN                   NaN   
2                         NaN      NaN                   NaN   
3                         NaN      NaN                   NaN   
4                         NaN      NaN                   NaN   
5                         NaN      NaN                   7.0   

        annotation network number best ion  auto MS2 verify  identified by n=  \
row ID                                                                          
1                             NaN      NaN              NaN               NaN   
2                             NaN      NaN              NaN               NaN   
3                             NaN      NaN              NaN               NaN   
4                             NaN      NaN              NaN               NaN   
5                             NaN      NaN              NaN               NaN   

        ... LQ-01-61-73_pos.mzXML Peak area  LQ-01-61-72_pos.mzXML Peak area  \
row ID  ...                                                                    
1       ...                             0.0                              0.0   
2       ...                             0.0                              0.0   
3       ...                             0.0                              0.0   
4       ...                             0.0                              0.0   
5       ...                             0.0                              0.0   

        LQ-01-61-54_pos.mzXML Peak area  LQ-01-61-75_pos.mzXML Peak area  \
row ID                                                                     
1                                  0.00                              0.0   
2                                  0.00                              0.0   
3                                  0.00                              0.0   
4                              36293.48                              0.0   
5                                  0.00                              0.0   

        LQ-01-61-58_pos.mzXML Peak area  LQ-01-61-55_pos.mzXML Peak area  \
row ID                                                                     
1                                   0.0                              0.0   
2                                   0.0                              0.0   
3                                   0.0                              0.0   
4                                   0.0                              0.0   
5                                   0.0                              0.0   

        LQ-01-61-74_pos.mzXML Peak area  LQ-01-61-56_pos.mzXML Peak area  \
row ID                                                                     
1                                   0.0                              0.0   
2                                   0.0                              0.0   
3                                   0.0                              0.0   
4                                   0.0                              0.0   
5                                   0.0                              0.0   

        LQ-01-61-37_pos.mzXML Peak area  Unnamed: 91  
row ID                                                
1                                   0.0          NaN  
2                                   0.0          NaN  
3                                   0.0          NaN  
4                                   0.0          NaN  
5                                   0.0          NaN  

[5 rows x 91 columns]

In [ ]:

#load table
df = 
def quant_table(df, filter = True, min_threshold = 0.5):
    """ Cleans up the quantitative table to specific format

    Args:
        df = quantitative.csv file, output from MZmine

    Returns:
        None
    """
    df.rename(columns = lambda x: x.replace(' Peak area', ''),inplace=True)
    df.drop(list(df.filter(regex = 'Unnamed:')), axis = 1, inplace = True)
    df.drop('row m/z', axis=1, inplace=True)
    df.drop('row retention time', axis=1, inplace=True)
    
    # vertical normalization by sample

    df = df.apply(lambda x: x/x.max(), axis=0)
    
    return df